### 모듈

In [40]:
import numpy as np
import pandas as pd
import ast
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report

### 데이터 불러오기

In [41]:
filenames = [
    "labeled_bond.csv",
    "labeled_economy.csv",
    "labeled_edaily.csv",
    "labeled_hk.csv",
    "labeled_infomax.csv",
    "labeled_mpb.csv"
]

df_list = []
for file in filenames:
    temp_df = pd.read_csv(file)
    df_list.append(temp_df)

# 모든 데이터가 합쳐진 최종 데이터프레임
df = pd.concat(df_list, ignore_index=True)

print(df.head())
print(df.shape)

         date                                        ngram_label
0  2024-11-29  [(('국내',), 22, -1), (('크레딧',), 7, -1), (('위험',...
1  2024-11-28  [(('투자자',), 10, -1), (('사전',), 3, -1), (('제공',...
2  2024-11-27  [(('채권',), 6, None), (('fed',), 10, None), (('...
3  2024-11-26  [(('글로벌',), 25, None), (('유동성',), 68, None), (...
4  2024-11-25  [(('외채',), 6, 1), (('전략',), 19, 1), (('유로존',),...
(15595, 2)


In [42]:
df['parsed'] = df['ngram_label'].apply(ast.literal_eval)

# 파싱된 열을 사용해서 각 라벨별 개수를 계산
none_count = df['parsed'].apply(lambda lst: sum(1 for item in lst if item[2] is None)).sum()
one_count = df['parsed'].apply(lambda lst: sum(1 for item in lst if item[2] == 1)).sum()
zero_count = df['parsed'].apply(lambda lst: sum(1 for item in lst if item[2] == 0)).sum()
minus_one_count = df['parsed'].apply(lambda lst: sum(1 for item in lst if item[2] == -1)).sum()

print("None 라벨 개수:", none_count)
print("1 라벨 개수:", one_count)
print("0 라벨 개수:", zero_count)
print("-1 라벨 개수:", minus_one_count)
print("총 개수:", none_count + one_count + zero_count + minus_one_count)

None 라벨 개수: 4202896
1 라벨 개수: 2515308
0 라벨 개수: 537207
-1 라벨 개수: 2068546
총 개수: 9323957


In [43]:
def parse_ngram_list(x):
    return ast.literal_eval(x)

In [46]:
df['ngram_list'] = df['ngram_label'].apply(parse_ngram_list)

### NBC 모델링

In [47]:
def create_document_and_target(ngram_list):
    if not ngram_list:
        return "", None
    
    # 초기화
    tokens = []
    target = None

    for item in ngram_list:
        token_tuple, freq, lab = item
        # item이 (('금리',), 13, 0) 형태일 때,
        # item[0] = 토큰 튜플
        # item[1] = 빈도수(freq)
        # item[2] = 라벨(-1이면 dovish, 1이면 hawkish)

        # 튜플을 문자열로 만들어 합친다.
        token_str = "_".join(token_tuple)
        if token_str not in tokens:
            tokens.append(token_str)

        if lab == 1:
            target = "hawkish"
        elif lab == -1:
            target = "dovish"

    document = " ".join(tokens) if tokens else ""
    return document, target

In [48]:
df[['document', 'target']] = df['ngram_list'].apply(lambda x: pd.Series(create_document_and_target(x)))
df = df.dropna(subset=['document', 'target'])
df.head()

date                                        ngram_label  \
0  2024-11-29  [(('국내',), 22, -1), (('크레딧',), 7, -1), (('위험',...   
1  2024-11-28  [(('투자자',), 10, -1), (('사전',), 3, -1), (('제공',...   
4  2024-11-25  [(('외채',), 6, 1), (('전략',), 19, 1), (('유로존',),...   
5  2024-11-22  [(('Fed',), 28, 1), (('fed',), 25, 1), (('대차대조...   
6  2024-11-21  [(('투자',), 3, 1), (('고객',), 3, 1), (('외국인',), ...   

                                              parsed  \
0  [((국내,), 22, -1), ((크레딧,), 7, -1), ((위험,), 25,...   
1  [((투자자,), 10, -1), ((사전,), 3, -1), ((제공,), 9, ...   
4  [((외채,), 6, 1), ((전략,), 19, 1), ((유로존,), 47, 1...   
5  [((Fed,), 28, 1), ((fed,), 25, 1), ((대차대조표,), ...   
6  [((투자,), 3, 1), ((고객,), 3, 1), ((외국인,), 5, 1),...   

                                          ngram_list  \
0  [((국내,), 22, -1), ((크레딧,), 7, -1), ((위험,), 25,...   
1  [((투자자,), 10, -1), ((사전,), 3, -1), ((제공,), 9, ...   
4  [((외채,), 6, 1), ((전략,), 19, 1), ((유로존,), 47, 1...   
5  [((Fed,), 28, 1), ((fed,), 25, 1), ((대차대조표,), ...   
6  [((투자,), 3, 1), ((고객,), 3, 1), ((외국인,), 5, 1),...   

                                            document   target  
0  국내 크레딧 위험 중심 유동성 이슈 추가 기대 유효 금통위 방향 등락 시장 금리 급...   dovish  
1  투자자 사전 제공 사실 내용 본인 의견 정확 반영 외부 부당 압력 간섭 없이 작성 ...   dovish  
4  외채 전략 유로존 인하 사이클 장기 경기 독일 제조업 중심 둔화 지속 우려 침체 상...  hawkish  
5  Fed fed 대차대조표 채권 주요 데이터 전체 자산 규모 증감 추이 보유 국채 축...  hawkish  
6  투자 고객 외국인 국채선물 국내 국채 금리 채권시장 동향 강세 마감 우려 하락 상승...  hawkish

### 학습

In [49]:
# 피처(X)와 타겟(y) 준비
X = df['document']
y = df['target']

# 학습/테스트 데이터 분리
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.1, random_state=42)

# CountVectorizer로 문서 벡터화
vectorizer = CountVectorizer()
X_train_vec = vectorizer.fit_transform(X_train)
X_test_vec = vectorizer.transform(X_test)

# 나이브 베이즈 분류기(MultinomialNB) 학습
clf = MultinomialNB()
clf.fit(X_train_vec, y_train)

# 테스트 데이터 예측 및 평가
y_pred = clf.predict(X_test_vec)
print(classification_report(y_test, y_pred))

              precision    recall  f1-score   support

      dovish       0.67      0.45      0.53       298
     hawkish       0.63      0.81      0.71       348

    accuracy                           0.64       646
   macro avg       0.65      0.63      0.62       646
weighted avg       0.65      0.64      0.63       646



In [50]:
feature_names = vectorizer.get_feature_names_out()
probs = np.exp(clf.feature_log_prob_)

In [51]:
sentiment_score = probs[1] - probs[0]

sentiment_df = pd.DataFrame({
    'feature': feature_names,
    'dovish_prob': probs[0],
    'hawkish_prob': probs[1],
    'sentiment_score': sentiment_score
})

print("Hawkish 쪽 상위 단어:")
print(sentiment_df.sort_values('sentiment_score', ascending=False).head(10))
print("\nDovish 쪽 상위 단어:")
print(sentiment_df.sort_values('sentiment_score', ascending=True).head(10))

Hawkish 쪽 상위 단어:
        feature  dovish_prob  hawkish_prob  sentiment_score
153006       긴축     0.000239      0.000417         0.000178
520505    인플레이션     0.000482      0.000582         0.000101
158339       내년     0.000395      0.000490         0.000095
48652     경기_침체     0.000190      0.000284         0.000094
233997       매파     0.000188      0.000273         0.000086
644474       집계     0.000299      0.000381         0.000082
436685       연말     0.000250      0.000329         0.000079
149932  기준금리_인상     0.000243      0.000322         0.000079
680977      코로나     0.000302      0.000379         0.000077
428034      에너지     0.000279      0.000355         0.000076

Dovish 쪽 상위 단어:
        feature  dovish_prob  hawkish_prob  sentiment_score
150525  기준금리_인하     0.000236      0.000135        -0.000101
422409     양적완화     0.000180      0.000094        -0.000086
116612    금리_인하     0.000488      0.000402        -0.000086
523474       인하     0.000657      0.000572        -0.000085
52319 

In [52]:
dovish_idx = np.where(clf.classes_ == 'dovish')[0][0]
hawkish_idx = np.where(clf.classes_ == 'hawkish')[0][0]

dovish_probs = probs[dovish_idx]
hawkish_probs = probs[hawkish_idx]

In [53]:
import numpy as np

N = 100000
# dovish에서 확률이 높은 단어 상위 N개
top_dovish_indices = np.argsort(dovish_probs)[::-1][:N]
top_dovish_words = [(feature_names[i], dovish_probs[i]) for i in top_dovish_indices]

# hawkish에서 확률이 높은 단어 상위 N개
top_hawkish_indices = np.argsort(hawkish_probs)[::-1][:N]
top_hawkish_words = [(feature_names[i], hawkish_probs[i]) for i in top_hawkish_indices]

print("===== Top Dovish Words =====")
for word, prob in top_dovish_words:
    print(word, prob)

print("===== Top Hawkish Words =====")
for word, prob in top_hawkish_words:
    print(word, prob)

===== Top Dovish Words =====
금리 0.0010180430820664217
미국 0.0010033393051304565
상승 0.0009673537457871735
경제 0.000955358559339413
투자 0.0009503283198613194
시장 0.0009302073619489464
하락 0.0009294334789523165
대비 0.000915890526511296
확대 0.0008934479196090339
증가 0.0008899654461242001
경기 0.000884935206646106
지속 0.0008717791957034009
국내 0.0008446932908213598
기준 0.0008431455248281008
기대 0.0008427585833297857
우려 0.0008319242213769692
추가 0.0008210898594241528
발표 0.0008110293804679664
유지 0.000806773023986503
규모 0.0008001950185151502
글로벌 0.0008001950185151502
관련 0.000793617013043797
정부 0.0007901345395589633
은행 0.0007878128905690741
가격 0.0007851043000808701
기업 0.0007835565340876104
정책 0.0007769785286162578
중국 0.0007742699381280538
주요 0.0007719482891381649
분기 0.0007676919326567007
국채 0.0007634355761752374
필요 0.0007587922781954591
분석 0.0007510534482291615
인상 0.0007483448577409575
감소 0.0007460232087510684
결과 0.0007448623842561234
투자자 0.0007448623842561234
채권 0.000744088501259494
대출 0.0007429276767645495


In [54]:
import pandas as pd

# 각 리스트에서 단어만 추출 (확률 정보는 제외)
dovish_words = [word for word, prob in top_dovish_words]
hawkish_words = [word for word, prob in top_hawkish_words]

df = pd.DataFrame({
    "dovish": pd.Series(dovish_words),
    "hawkish": pd.Series(hawkish_words)
})

# CSV 파일로 저장 (index 없이 저장)
df.to_csv("word_dictionary.csv", index=False)